In [3]:
from pathlib import Path
import os
import pandas as pd
import numpy as np
import cv2

os.chdir(Path(os.getcwd()).parent)

from src.data_proc.keypoints import KeypointProcessing
import networkx as nx
import matplotlib.pyplot as plt

In [42]:
class KeypointProcessingGraph(KeypointProcessing):
    def __init__(self):
        self.backend = 'onnxruntime'
        self.device = 'cuda'
        self.openpose= True

        # skeleton de COCO + manos
        # topología COCO-25 (pose + cuello + cabeza) 
        BODY_CONNECTIONS = [
            (1,2), (1, 5), (5, 6), (6, 7),
            # Cabeza y Cuello
            # (24, 0), (0, 23), (0, 1), (0, 2), (1, 3), (2, 4),
            # Torso
            # (23, 5), (23, 6), (5, 6), (5, 11), (6, 12), (11, 12),
            # Brazos
            # (5, 7), (7, 9), (6, 8), (8, 10),
        ]

        # 2. Rostro (se conectan secuencialmente)
        FACE_CONNECTIONS = (
            # Mandíbula
            list(zip(range(24, 41), range(26, 42))) +
            # Ceja Derecha
            list(zip(range(42, 46), range(43, 47))) +
            # Ceja Izquierda
            list(zip(range(47, 51), range(48, 52))) +
            # Puente de la Nariz
            list(zip(range(52, 55), range(53, 56))) +
            # Nariz Inferior
            list(zip(range(56, 60), range(57, 61))) +
            # Ojo Derecho (con cierre)
            list(zip(range(61, 66), range(62, 67))) + [(66, 61)] +
            # Ojo Izquierdo (con cierre)
            list(zip(range(67, 72), range(68, 73))) + [(72, 67)] +
            # Labio Exterior (con cierre)
            list(zip(range(73, 84), range(74, 85))) + [(84, 73)] +
            # Labio Interior (con cierre)
            list(zip(range(85, 94), range(86, 95))) + [(94, 85)]
        )

        # 3. Manos y conexión con los brazos
        HAND_CONNECTIONS = [
            # Conexión Brazo -> Mano
            (2, 3), (3, 4),
            # Mano Izquierda
            (7, 92), (7, 97), (7, 101), (7, 105), (7, 109),      # Palma
            (92, 93), (93, 94), (94, 95), (95, 96),               # Pulgar
            (97, 98), (98, 99), (99, 100),                        # Índice
            (101, 102), (102, 103), (103, 104),                   # Medio
            (105, 106), (106, 107), (107, 108),                   # Anular
            (109, 110), (110, 111), (111, 112),                   # Meñique
            # Mano Derecha
            (113, 114), (114, 115), (115, 116), (116, 117),                    # Meñique
            (118, 119), (119, 120), (120, 121),
            (118, 119), (119, 120), (120, 121),                         # Pulgar
            (122, 123), (123, 124),                                     # Índice
            (126, 127), (127, 128), (128, 129),                         # Anular
            (130, 131), (131, 132), (132, 133),                         # Meñique
            (4, 118), (4, 122), (4, 126), (4, 130), (4, 113)  # Palma
        ]


        # combinamos todo
        self.SKELETON = HAND_CONNECTIONS + BODY_CONNECTIONS # + FACE_CONNECTIONS + HAND_CONNECTIONS

    def load_model(self):
        from rtmlib import Custom
        self.model = Custom(
            to_openpose=self.openpose,
            det_class='RTMDet',
            det='https://download.openmmlab.com/mmpose/v1/projects/rtmposev1/onnx_sdk/yolox_x_8xb8-300e_humanart-a39d44ed.zip',
            det_input_size=(640, 640),
            pose_class='RTMPose',
            pose='https://download.openmmlab.com/mmpose/v1/projects/rtmposev1/onnx_sdk/rtmpose-l_simcc-ucoco_dw-ucoco_270e-384x288-2438fd99_20230728.zip',
            pose_input_size=(288, 384),
            backend=self.backend,
            device=self.device,
        )

    def build_skeleton_graph(self, keypoints):
        G = nx.Graph()
        for i, (x, y) in enumerate(keypoints):
            G.add_node(i, coord=(x, y))
        for i, j in self.SKELETON:
            if i < len(keypoints) and j < len(keypoints):
                G.add_edge(i, j)
        return G

    def draw_skeleton(self, frame_img, keypoints, G):
        for i, j in G.edges:
            xi, yi = keypoints[i]
            xj, yj = keypoints[j]
            if all(v >= 0 for v in [xi, yi, xj, yj]):
                cv2.line(frame_img, (int(xi), int(yi)), (int(xj), int(yj)), (0, 255, 0), 2)

        for i, (x, y) in enumerate(keypoints):
            if x >= 0 and y >= 0:
                cv2.circle(frame_img, (int(x), int(y)), 2, (0, 0, 255), -1)
                cv2.putText(
                    frame_img,
                    str(i),
                    (int(x) + 5, int(y) - 5),
                    cv2.FONT_HERSHEY_SIMPLEX,
                    0.4,
                    (255, 255, 0),
                    1,
                    cv2.LINE_AA
                )
        return frame_img

    def export_skeleton_video(self, input_video_path, keypoints_array, output_path='output.mp4'):
        cap = cv2.VideoCapture(input_video_path)
        fps = cap.get(cv2.CAP_PROP_FPS)
        w  = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
        h  = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
        out = cv2.VideoWriter(output_path, cv2.VideoWriter_fourcc(*'mp4v'), fps, (w, h))

        for i in range(len(keypoints_array)):
            ret, frame = cap.read()
            if not ret: break
            keypoints = keypoints_array[i]
            G = self.build_skeleton_graph(keypoints)
            frame_out = self.draw_skeleton(frame, keypoints, G)
            out.write(frame_out)

        cap.release()
        out.release()

In [ ]:
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

filename = "./wasap.mp4"
kp = KeypointProcessingGraph()
kp.load_model()
keypoints_array = kp.process_keypoints(filename)

# 2. Extraer el primer frame del video original
cap = cv2.VideoCapture(filename)
fps = cap.get(cv2.CAP_PROP_FPS)

# Limitar el número de frames para que la animación no sea muy pesada (opcional)
num_frames_a_procesar = len(keypoints_array)

# Crear la figura y el eje sobre el que se animará
fig, ax = plt.subplots(figsize=(9, 16), dpi=150)
ax.axis('off') # Ocultar ejes

# Leer el primer frame para inicializar la imagen
ret, first_frame = cap.read()
if not ret:
    raise ValueError("No se pudo leer el video.")

# Mostrar el primer frame (convertido a RGB)
im = ax.imshow(cv2.cvtColor(first_frame, cv2.COLOR_BGR2RGB))
plt.close(fig) # Evita que se muestre una figura estática extra

# Reiniciar el video para leerlo desde el principio en la función de animación
cap.set(cv2.CAP_PROP_POS_FRAMES, 0)

# 3. Definir la función que actualiza cada frame de la animación
def update(frame_index):
    ret, frame = cap.read()
    if not ret:
        return [im] # Termina si no hay más frames

    # Obtener los keypoints para el frame actual
    keypoints = keypoints_array[frame_index]
    
    # Dibujar el esqueleto
    G = kp.build_skeleton_graph(keypoints)
    frame_con_esqueleto = kp.draw_skeleton(frame, keypoints, G)
    
    # Convertir a RGB y actualizar los datos de la imagen
    frame_rgb = cv2.cvtColor(frame_con_esqueleto, cv2.COLOR_BGR2RGB)
    im.set_data(frame_rgb)
    
    # Actualizar el título para ver el progreso
    ax.set_title(f"Frame: {frame_index + 1}/{num_frames_a_procesar}")
    
    return [im]

# 4. Crear y mostrar la animación
anim = FuncAnimation(
    fig,
    update,
    frames=num_frames_a_procesar,
    interval=1000/fps, # Intervalo entre frames en milisegundos
    blit=True
)

# Convertir la animación a video HTML5 para mostrarla en el notebook
html_video = HTML(anim.to_html5_video())

# Liberar el video
cap.release()

# Mostrar el video en la celda
html_video

2025-08-02 13:27:02.535384850 [W:onnxruntime:, session_state.cc:1280 VerifyEachNodeIsAssignedToAnEp] Some nodes were not assigned to the preferred execution providers which may or may not have an negative impact on performance. e.g. ORT explicitly assigns shape related ops to CPU to improve perf.
2025-08-02 13:27:02.535395419 [W:onnxruntime:, session_state.cc:1282 VerifyEachNodeIsAssignedToAnEp] Rerunning with verbose output on a non-minimal build will show node assignments.
2025-08-02 13:27:02.699938728 [W:onnxruntime:, session_state.cc:1280 VerifyEachNodeIsAssignedToAnEp] Some nodes were not assigned to the preferred execution providers which may or may not have an negative impact on performance. e.g. ORT explicitly assigns shape related ops to CPU to improve perf.
2025-08-02 13:27:02.699948777 [W:onnxruntime:, session_state.cc:1282 VerifyEachNodeIsAssignedToAnEp] Rerunning with verbose output on a non-minimal build will show node assignments.


load /home/giorgio6846/.cache/rtmlib/hub/checkpoints/yolox_x_8xb8-300e_humanart-a39d44ed.onnx with onnxruntime backend
load /home/giorgio6846/.cache/rtmlib/hub/checkpoints/rtmpose-l_simcc-ucoco_dw-ucoco_270e-384x288-2438fd99_20230728.onnx with onnxruntime backend
Video:  ./wasap.mp4


Frames 0-571:   3%|▎         | 17/572 [00:00<00:25, 21.68it/s]

Frames 0-571: 100%|██████████| 572/572 [00:19<00:00, 28.66it/s]


Likely signer: 0 with total hand movement: 79551.12613070299


In [13]:
filename = "../data/raw/dataset1/videos/001_001_002.mp4"
kp = KeypointProcessingGraph()
kp.load_model()
keypoints_array = kp.process_keypoints(filename)

# Extraer frame original (opcional)
video = cv2.VideoCapture(filename)
ret, frame0 = video.read()
video.release()

# Usar el primer frame
keypoints = keypoints_array[0]  # (K,2)
G = kp.build_skeleton_graph(keypoints)
# kp.draw_skeleton(frame0, keypoints, G)
kp.export_skeleton_video(filename, keypoints_array, "/home/giorgio6846/Code/Sign-AI/Sign-chris/notebooks/outputs/output2.mp4")


2025-08-02 12:02:05.090015644 [W:onnxruntime:, session_state.cc:1280 VerifyEachNodeIsAssignedToAnEp] Some nodes were not assigned to the preferred execution providers which may or may not have an negative impact on performance. e.g. ORT explicitly assigns shape related ops to CPU to improve perf.
2025-08-02 12:02:05.090027005 [W:onnxruntime:, session_state.cc:1282 VerifyEachNodeIsAssignedToAnEp] Rerunning with verbose output on a non-minimal build will show node assignments.
2025-08-02 12:02:05.256894200 [W:onnxruntime:, session_state.cc:1280 VerifyEachNodeIsAssignedToAnEp] Some nodes were not assigned to the preferred execution providers which may or may not have an negative impact on performance. e.g. ORT explicitly assigns shape related ops to CPU to improve perf.
2025-08-02 12:02:05.256906253 [W:onnxruntime:, session_state.cc:1282 VerifyEachNodeIsAssignedToAnEp] Rerunning with verbose output on a non-minimal build will show node assignments.


load /home/giorgio6846/.cache/rtmlib/hub/checkpoints/yolox_x_8xb8-300e_humanart-a39d44ed.onnx with onnxruntime backend
load /home/giorgio6846/.cache/rtmlib/hub/checkpoints/rtmpose-l_simcc-ucoco_dw-ucoco_270e-384x288-2438fd99_20230728.onnx with onnxruntime backend
Video:  ../data/raw/dataset1/videos/001_001_002.mp4


Frames 0-147: 100%|██████████| 148/148 [00:05<00:00, 28.30it/s]


Likely signer: 0 with total hand movement: 1945.2811132218326
